# Finetuning efficientNet

Lets try the model that is trending for image classification on HuggingFace: efficientnet_b2.ra_in1k

In [1]:
from datasets import load_dataset

cifar10dataset = load_dataset("cifar10", split="train")

Generating train split:   0%|          | 0/50000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/10000 [00:00<?, ? examples/s]

In [2]:
cifar10dataset = cifar10dataset.train_test_split(test_size=0.2)

In [3]:
labels = cifar10dataset["train"].features["label"].names
label2id, id2label = dict(), dict()
for i, label in enumerate(labels):
    label2id[label] = str(i)
    id2label[str(i)] = label

In [4]:
from transformers import AutoImageProcessor

# import timm
# model = timm.create_model("hf_hub:timm/efficientnet_b2.ra_in1k", pretrained=True)

checkpoint = "google/efficientnet-b3"
image_processor = AutoImageProcessor.from_pretrained(checkpoint)

In [5]:
from torchvision.transforms import RandomResizedCrop, Compose, Normalize, ToTensor

normalize = Normalize(mean=image_processor.image_mean, std=image_processor.image_std)
size = (
    image_processor.size["shortest_edge"]
    if "shortest_edge" in image_processor.size
    else (image_processor.size["height"], image_processor.size["width"])
)
_transforms = Compose([RandomResizedCrop(size), ToTensor(), normalize])

In [6]:
def transforms(examples):
    examples["pixel_values"] = [_transforms(img.convert("RGB")) for img in examples["img"]]
    del examples["img"]
    return examples

In [14]:
import pandas as pd
import os

file2obj = pd.read_csv("../data/processed/OM_file_to_obj.csv")
file2obj["image"] = file2obj.apply(lambda x: os.path.join("..", x["root"], x["file"]), axis=1)

# Group by 'obj_num' and count occurrences
obj_num_counts = file2obj["obj_num"].value_counts()

# Filter rows where 'obj_num' appears more than twice
file2obj_3 = file2obj[file2obj["obj_num"].isin(obj_num_counts[obj_num_counts > 2].index)]

In [15]:
from datasets import Dataset, Image, DatasetDict


ds = Dataset.from_pandas(file2obj_3[["image", "obj_num"]], preserve_index=False).cast_column(
    "image", Image()
)
ds = ds.class_encode_column("obj_num")
trainval_test = ds.train_test_split(stratify_by_column="obj_num", test_size=0.16)
train_val = trainval_test["train"].train_test_split(
    stratify_by_column="obj_num", test_size=16 / 84
)
ds = DatasetDict(
    {"train": train_val["train"], "valid": train_val["test"], "test": trainval_test["test"]}
)

Casting to class labels:   0%|          | 0/25725 [00:00<?, ? examples/s]

In [17]:
cifar10dataset = cifar10dataset.with_transform(transforms)
# cifar10dataset = ds.map(transforms)

In [ ]:
from transformers import DefaultDataCollator

data_collator = DefaultDataCollator()

In [ ]:
import evaluate

accuracy = evaluate.load("accuracy")

In [ ]:
import numpy as np


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=labels)

In [ ]:
from transformers import AutoModelForImageClassification, TrainingArguments, Trainer

model = AutoModelForImageClassification.from_pretrained(
    checkpoint,
    num_labels=len(labels),
    ignore_mismatched_sizes=True,
    id2label=id2label,
    label2id=label2id,
)

Some weights of EfficientNetForImageClassification were not initialized from the model checkpoint at google/efficientnet-b3 and are newly initialized because the shapes did not match:
- classifier.weight: found shape torch.Size([1000, 1536]) in the checkpoint and torch.Size([10, 1536]) in the model instantiated
- classifier.bias: found shape torch.Size([1000]) in the checkpoint and torch.Size([10]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
import torch

torch.cuda.empty_cache()

In [ ]:
training_args = TrainingArguments(
    output_dir="cifar10_efficientnet",
    remove_unused_columns=False,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    learning_rate=5e-5,
    per_device_train_batch_size=8,  # memory error with 16
    gradient_accumulation_steps=4,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    warmup_ratio=0.1,
    logging_steps=10,
    load_best_model_at_end=True,
    metric_for_best_model="accuracy",
    push_to_hub=False,
)

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=cifar10dataset["train"],
    eval_dataset=cifar10dataset["test"],
    tokenizer=image_processor,
    compute_metrics=compute_metrics,
)

trainer.train()

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: jameswburton18. Use `wandb login --relogin` to force relogin


  0%|          | 0/3750 [00:00<?, ?it/s]

{'loss': 2.3286, 'learning_rate': 1.3333333333333334e-06, 'epoch': 0.01}


KeyboardInterrupt: 

### Evaluation

In [ ]:
results = trainer.evaluate()
print(results)

test_results = trainer.predict(